In [2]:
:dep plotters = { version = "^0.3.0", default_features = false, features = ["evcxr", "all_series"] }
:dep serde = { version = "1.0.103", features = ["derive"] }
:dep serde_json = "1.0.85"
extern crate plotters;
extern crate serde;
extern crate serde_json;
// Import all the plotters prelude functions
use plotters::prelude::*;
use serde::{Serialize, Deserialize};


#[derive(Serialize, Deserialize)]
pub struct CircSerde {
    pub guard: String,
    pub middle: String,
    pub exit: String,
}

let tor_ps_path = "circs_torps_test.txt";
let tor_ps_circs_str = std::fs::read_to_string(&tor_ps_path).unwrap();
let tor_ps_circs : Vec<CircSerde> = serde_json::from_str(&tor_ps_circs_str).unwrap();


evcxr_figure((320,50), |root| {
    root.fill(&GREEN)?;
    root.draw(&Text::new("Hello World from Plotters!", (15, 15), ("Arial", 20).into_font()))?;
    Ok(())
})

Hello World from Plotters!

In [3]:
:dep plotters = { version = "^0.3.0", default_features = false, features = ["evcxr", "all_series", "all_elements"] }
:dep serde = { version = "1.0.103", features = ["derive"] }
:dep serde_json = "1.0.85"
extern crate plotters;
extern crate serde;
extern crate serde_json;
// Import all the plotters prelude functions
use plotters::prelude::*;
use serde::{Serialize, Deserialize};
use std::collections::HashMap;


#[derive(Serialize, Deserialize)]
pub struct CircSerde {
    pub guard: String,
    pub middle: String,
    pub exit: String,
}
#[derive(Default)]
pub struct SimulationSource{
    gen: usize,
    torps: usize
}
fn circs_to_map(gen_circs: &Vec<CircSerde>, torps_circs: &Vec<CircSerde>) -> HashMap<String, SimulationSource> {
    let mut tor_relays_map : HashMap<String, SimulationSource> = HashMap::new();
    for circ in gen_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().gen += 1;
    }
    for circ in torps_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().torps += 1;
    }
    tor_relays_map    
}

fn map_to_combined_histo(map: &HashMap<String,SimulationSource>) -> (Vec<(usize,usize,usize)>, usize){
    let mut histo : Vec<(usize,usize,usize)> = vec![];
    let mut index = 0;
    let mut max = 0;
    for (relay, source) in map {
        if source.gen > max {
            max = source.gen;
        }
        if source.torps > max {
            max = source.torps;
        }
        histo.push((index, source.gen, source.torps));
        index += 1;
    }
    (histo, max)
}
let tor_ps_path = "circs_torps";
let tor_gen_path = "circs_generated";
let tor_ps_circs_str = std::fs::read_to_string(&tor_ps_path).unwrap();
let tor_gen_circs_str = std::fs::read_to_string(&tor_gen_path).unwrap();
let tor_ps_circs : Vec<CircSerde> = serde_json::from_str(&tor_ps_circs_str).unwrap();
let tor_gen_circs : Vec<CircSerde> = serde_json::from_str(&tor_gen_circs_str).unwrap();
let relay_map = circs_to_map(&tor_gen_circs, &tor_ps_circs);
let (relay_histo, max_count) = map_to_combined_histo(&relay_map);

evcxr_figure((640, 480), |root| {
    let areas = root.split_evenly((2,1));
    let mut charts = vec![];
    
    // The following code will create a chart context
    let mut chart = ChartBuilder::on(&areas[0])
            .caption(format!("Histogram for TorPS"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(40)
            .build_cartesian_2d(0usize..relay_histo.len(), 0usize..max_count)?;
        chart.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_labels(5)
            .draw()?;
        charts.push(chart);
    let mut chart = ChartBuilder::on(&areas[1])
            .caption(format!("Histogram for Tor Circuit Generator"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(40)
            .build_cartesian_2d(0usize..relay_histo.len(), 0usize..max_count)?;
        chart.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_labels(5)
            .draw()?;
        charts.push(chart);
    
    charts[0].draw_series(
        relay_histo.iter().map(|(idx, gen, torps)| Circle::new((*idx,*gen), 1, &BLUE)),
    )
    .unwrap();
    
       charts[1].draw_series(
        relay_histo.iter().map(|(idx, gen, torps)| Circle::new((*idx,*torps), 1, &RED)),
    )
    .unwrap();

    Ok(())
}).style("width:100%")

The type of the variable tor_ps_circs was redefined, so was lost.


Histogram for TorPS
 
 
 
0
 
 
 
5000
 
 
 
 
0
 
 
 
500
 
 
 
1000
 
 
 
1500
 
 
 
2000
 
 
 
2500
 
 
 
3000
 
 
 
3500
 
 
 
4000
 
 
 
4500
 
 
 
Histogram for Tor Circuit Generator
 
 
 
0
 
 
 
5000
 
 
 
 
0
 
 
 
500
 
 
 
1000
 
 
 
1500
 
 
 
2000
 
 
 
2500
 
 
 
3000
 
 
 
3500
 
 
 
4000
 
 
 
4500
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 


In [4]:
#[derive(Serialize,Deserialize)]
pub struct SerdeRelay {
    pub fingerprint: String,
    pub bandwidth: u64,
    pub flags: Vec<String>,
    pub nickname: String,
}

let relay_info_path = "relays";

let relay_info_str = std::fs::read_to_string(&relay_info_path).unwrap();
let relay_info_vec : Vec<SerdeRelay> = serde_json::from_str(&relay_info_str).unwrap();
let mut relay_info_map : HashMap<String, SerdeRelay> = HashMap::new();
relay_info_vec.into_iter().for_each(|r| {relay_info_map.insert(r.fingerprint.clone(), r);});


In [11]:
#[derive(Default)]
struct CompSimSource {
    gen : Vec<usize>,
    torps: Vec<usize>,
}
let tor_ps_path = "circs_torps";
let tor_gen_path = "circs_generated";
let tor_ps_circs_str = std::fs::read_to_string(&tor_ps_path).unwrap();
let tor_gen_circs_str = std::fs::read_to_string(&tor_gen_path).unwrap();
let tor_ps_circs : Vec<CircSerde> = serde_json::from_str(&tor_ps_circs_str).unwrap();
let tor_gen_circs : Vec<CircSerde> = serde_json::from_str(&tor_gen_circs_str).unwrap();
let mut compMap : HashMap<String, CompSimSource> = HashMap::new();
let relay_map = circs_to_map(&tor_gen_circs, &tor_ps_circs);
for (relay, source) in relay_map.iter() {
        let nickname = relay_info_map.get(relay).unwrap().nickname.clone();
    compMap.entry(nickname.clone()).or_default().gen.push(source.gen);
    compMap.entry(nickname).or_default().torps.push(source.torps);
}

fn find_differences_zero_circuits(map: &HashMap<String,CompSimSource>, relay_info_map: &HashMap<String, SerdeRelay>) -> (Vec<String>, usize){
    let mut nicknames: Vec<String> = vec![];
    let mut max = 0;
    
    for (nickname, source) in map {
        let gen_sum = source.gen.iter().sum::<usize>();
        let ps_sum = source.torps.iter().sum::<usize>();
        if gen_sum.abs_diff(ps_sum) > 5 && (gen_sum == 0 || ps_sum == 0) {
            let nickname_max = source.gen.iter().chain(source.torps.iter()).max().or(Some(&0)).unwrap().clone();
             if nickname_max > max {
                max = nickname_max;
            }
            nicknames.push(nickname.clone());
        }
    };
    nicknames.push(String::from(""));
        nicknames.push(String::from(""));
        nicknames.push(String::from(""));
    (nicknames, max)
}

let (mut nicknames, max) = find_differences_zero_circuits(&compMap, &relay_info_map);
    println!("{}", nicknames.len());
evcxr_figure((900, 3000), |root| {
    let mut charts = vec![];
    // The following code will create a chart context
    let mut chart = ChartBuilder::on(&root)
            .caption(format!("Compared Histogram for TorPS"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(250)
            .build_cartesian_2d(0usize..(max+5), 0usize..(nicknames.len()-1))?;
        chart.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_label_formatter(&|x| format!("{}", nicknames[*x].clone()))
            .y_labels(nicknames.len())
            .draw()?;
        charts.push(chart);
    let mut i = 0;
    for nickname in nicknames.iter() {
        if nickname.eq("") {
            continue;
        }
        charts[0].draw_series(
            compMap.get(nickname).unwrap().gen.iter().map(|gen| Circle::new((*gen, i), 3, &BLUE)),
        )
    .unwrap();
        charts[0].draw_series(
            compMap.get(nickname).unwrap().torps.iter().map(|torps| Circle::new((*torps, i), 3, &RED)),
        )
    .unwrap();
        i += 1;
    }
    Ok(())
}).style("width:100%")

5


Compared Histogram for TorPS
 
 
 
youareidiot
 
 
 
Cebollero
 
 
 

 
 
 

 
 
 

 
 
 
 
0
 
 
 
50
 
 
 
100
 
 
 
150
 
 
 
200
 
 
 
250
 
 
 
300
 
 
 
350
 
 
 
400

In [8]:
:dep plotters = { version = "^0.3.0", default_features = false, features = ["evcxr", "all_series", "all_elements"] }
:dep serde = { version = "1.0.103", features = ["derive"] }
:dep serde_json = "1.0.85"
extern crate plotters;
extern crate serde;
extern crate serde_json;
// Import all the plotters prelude functions
use plotters::prelude::*;
use serde::{Serialize, Deserialize};
use std::collections::HashMap;


#[derive(Serialize, Deserialize)]
pub struct CircSerde {
    pub guard: String,
    pub middle: String,
    pub exit: String,
}
#[derive(Default)]
pub struct SimulationSource{
    gen: usize,
    torps: usize
}
fn circs_to_map(gen_circs: &Vec<CircSerde>, torps_circs: &Vec<CircSerde>) -> HashMap<String, SimulationSource> {
    let mut tor_relays_map : HashMap<String, SimulationSource> = HashMap::new();
    for circ in gen_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().gen += 1;
    }
    for circ in torps_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().torps += 1;
    }
    tor_relays_map    
}

fn map_to_combined_histo(map: &HashMap<String,SimulationSource>) -> (Vec<(usize,usize,usize)>, usize){
    let mut histo : Vec<(usize,usize,usize)> = vec![];
    let mut index = 0;
    let mut max = 0;
    for (relay, source) in map {
        if source.gen > max {
            max = source.gen;
        }
        if source.torps > max {
            max = source.torps;
        }
        histo.push((index, source.gen, source.torps));
        index += 1;
    }
    (histo, max)
}
let tor_ps_path = "circs_torps";
let tor_gen_path = "circs_generated";
let tor_ps_circs_str = std::fs::read_to_string(&tor_ps_path).unwrap();
let tor_gen_circs_str = std::fs::read_to_string(&tor_gen_path).unwrap();
let tor_ps_circs : Vec<CircSerde> = serde_json::from_str(&tor_ps_circs_str).unwrap();
let tor_gen_circs : Vec<CircSerde> = serde_json::from_str(&tor_gen_circs_str).unwrap();
let relay_map = circs_to_map(&tor_gen_circs, &tor_ps_circs);
let (relay_histo, max_count) = map_to_combined_histo(&relay_map);

evcxr_figure((640, 480), |root| {
    let areas = root.split_evenly((2,1));
    let mut charts = vec![];
    
    // The following code will create a chart context
    let mut chart = ChartBuilder::on(&areas[0])
            .caption(format!("Histogram for TorPS"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(40)
            .build_cartesian_2d(0usize..relay_histo.len(), 0usize..max_count)?;
        chart.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_labels(5)
            .draw()?;
        charts.push(chart);
    let mut chart = ChartBuilder::on(&areas[1])
            .caption(format!("Histogram for Tor Circuit Generator"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(40)
            .build_cartesian_2d(0usize..relay_histo.len(), 0usize..max_count)?;
        chart.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_labels(5)
            .draw()?;
        charts.push(chart);
    
    charts[0].draw_series(
        relay_histo.iter().map(|(idx, gen, torps)| Circle::new((*idx,*gen), 1, &BLUE)),
    )
    .unwrap();
    
       charts[1].draw_series(
        relay_histo.iter().map(|(idx, gen, torps)| Circle::new((*idx,*torps), 1, &RED)),
    )
    .unwrap();

    Ok(())
}).style("width:100%")

Histogram for TorPS
 
 
 
0
 
 
 
5000
 
 
 
 
0
 
 
 
500
 
 
 
1000
 
 
 
1500
 
 
 
2000
 
 
 
2500
 
 
 
3000
 
 
 
3500
 
 
 
4000
 
 
 
4500
 
 
 
Histogram for Tor Circuit Generator
 
 
 
0
 
 
 
5000
 
 
 
 
0
 
 
 
500
 
 
 
1000
 
 
 
1500
 
 
 
2000
 
 
 
2500
 
 
 
3000
 
 
 
3500
 
 
 
4000
 
 
 
4500
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 


In [23]:
:dep plotters = { version = "^0.3.0", default_features = false, features = ["evcxr", "all_series", "all_elements"] }
:dep serde = { version = "1.0.103", features = ["derive"] }
:dep serde_json = "1.0.85"
extern crate plotters;
extern crate serde;
extern crate serde_json;
// Import all the plotters prelude functions
use plotters::prelude::*;
use serde::{Serialize, Deserialize};
use std::collections::HashMap;


#[derive(Serialize, Deserialize)]
pub struct CircSerde {
    pub guard: String,
    pub middle: String,
    pub exit: String,
}
#[derive(Default, Clone)]
pub struct SimulationSource{
    gen: usize,
    torps: usize
}
fn circs_to_map(gen_circs: &Vec<CircSerde>, torps_circs: &Vec<CircSerde>) -> HashMap<String, SimulationSource> {
    let mut tor_relays_map : HashMap<String, SimulationSource> = HashMap::new();
    for circ in gen_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().gen += 1;
    }
    for circ in torps_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().torps += 1;
    }
    tor_relays_map    
}

fn map_to_combined_histo(map: &HashMap<String,SimulationSource>) -> (Vec<(usize,usize,usize)>, usize){
    let mut histo : Vec<(usize,usize,usize)> = vec![];
    let mut index = 0;
    let mut max = 0;
    for (relay, source) in map {
        if source.gen > max {
            max = source.gen;
        }
        if source.torps > max {
            max = source.torps;
        }
        histo.push((index, source.gen, source.torps));
        index += 1;
    }
    (histo, max)
}

fn cdf(x: &[usize]) -> Vec<(usize, f64)> {
    let ln = x.len() as f64;
    let mut x_ord = x.to_vec();
    x_ord.sort_by(|a, b| a.partial_cmp(b).unwrap());
    let mut cdf = Vec::new();
    for (i,pos) in x.iter().enumerate() {
        let num = x_ord.iter().filter(|x| **x <= i).count() as f64;
        cdf.push((i, num/ln,));
    }
    println!("Len: {ln} Len cdf: {}", cdf.len());
    cdf
}

let tor_ps_path = "circs_torps";
let tor_gen_path = "circs_generated";
let tor_ps_circs_str = std::fs::read_to_string(&tor_ps_path).unwrap();
let tor_gen_circs_str = std::fs::read_to_string(&tor_gen_path).unwrap();
let tor_ps_circs : Vec<CircSerde> = serde_json::from_str(&tor_ps_circs_str).unwrap();
let tor_gen_circs : Vec<CircSerde> = serde_json::from_str(&tor_gen_circs_str).unwrap();
let relay_map = circs_to_map(&tor_gen_circs, &tor_ps_circs);

let tor_ps_vec: Vec<usize> = relay_map.values().cloned().map(|x| x.torps).collect();
let tor_ps_cdf : Vec<(usize, f64)> = cdf(&tor_ps_vec);

let tor_gen_vec: Vec<usize> = relay_map.values().cloned().map(|x| x.gen).collect();
let tor_gen_cdf : Vec<(usize, f64)> = cdf(&tor_gen_vec);
//let (relay_histo, max_count) = map_to_combined_histo(&relay_map);

evcxr_figure((640, 480), |root| {
    let areas = root.split_evenly((2,1));
    let mut charts = vec![];
    
    // The following code will create a chart context
    let mut chart = ChartBuilder::on(&areas[0])
            .caption(format!("CDF for TorPS"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(40)
            .build_cartesian_2d(0usize..tor_ps_vec.len(), 0f64..1f64)?;
        chart.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_labels(5)
            .draw()?;
        charts.push(chart);
    
      let mut chart2 = ChartBuilder::on(&areas[1])
            .caption(format!("CDF for TorGen"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(40)
            .build_cartesian_2d(0usize..tor_gen_vec.len(), 0f64..1f64)?;
        chart2.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_labels(5)
            .draw()?;
        charts.push(chart2);
    
    charts[0].draw_series(
        tor_ps_cdf.iter().map(|(idx, torps)| Circle::new((*idx,*torps), 1, &BLUE)),
    )
    .unwrap();
    charts[1].draw_series(
        tor_gen_cdf.iter().map(|(idx, torgen)| Circle::new((*idx,*torgen), 1, &RED)),
    )
    .unwrap();
    

    Ok(())
}).style("width:100%")

Len: 4693 Len cdf: 4693
Len: 4693 Len cdf: 4693


CDF for TorPS
 
 
 
0.0
 
 
 
0.5
 
 
 
1.0
 
 
 
 
0
 
 
 
500
 
 
 
1000
 
 
 
1500
 
 
 
2000
 
 
 
2500
 
 
 
3000
 
 
 
3500
 
 
 
4000
 
 
 
4500
 
 
 
CDF for TorGen
 
 
 
0.0
 
 
 
0.5
 
 
 
1.0
 
 
 
 
0
 
 
 
500
 
 
 
1000
 
 
 
1500
 
 
 
2000
 
 
 
2500
 
 
 
3000
 
 
 
3500
 
 
 
4000
 
 
 
4500
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 

In [24]:
:dep plotters = { version = "^0.3.0", default_features = false, features = ["evcxr", "all_series", "all_elements"] }
:dep serde = { version = "1.0.103", features = ["derive"] }
:dep serde_json = "1.0.85"
extern crate plotters;
extern crate serde;
extern crate serde_json;
// Import all the plotters prelude functions
use plotters::prelude::*;
use serde::{Serialize, Deserialize};
use std::collections::HashMap;


#[derive(Serialize, Deserialize)]
pub struct CircSerde {
    pub guard: String,
    pub middle: String,
    pub exit: String,
}
#[derive(Default, Clone)]
pub struct SimulationSource{
    gen: usize,
    torps: usize
}
fn circs_to_map(gen_circs: &Vec<CircSerde>, torps_circs: &Vec<CircSerde>) -> HashMap<String, SimulationSource> {
    let mut tor_relays_map : HashMap<String, SimulationSource> = HashMap::new();
    for circ in gen_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().gen += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().gen += 1;
    }
    for circ in torps_circs {
        tor_relays_map.entry(circ.guard.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.middle.clone()).or_default().torps += 1;
        tor_relays_map.entry(circ.exit.clone()).or_default().torps += 1;
    }
    tor_relays_map    
}

fn map_to_combined_histo(map: &HashMap<String,SimulationSource>) -> (Vec<(usize,usize,usize)>, usize){
    let mut histo : Vec<(usize,usize,usize)> = vec![];
    let mut index = 0;
    let mut max = 0;
    for (relay, source) in map {
        if source.gen > max {
            max = source.gen;
        }
        if source.torps > max {
            max = source.torps;
        }
        histo.push((index, source.gen, source.torps));
        index += 1;
    }
    (histo, max)
}

fn cdf(x: &[usize]) -> Vec<(usize, f64)> {
    let ln = x.len() as f64;
    let mut x_ord = x.to_vec();
    x_ord.sort_by(|a, b| a.partial_cmp(b).unwrap());
    let mut cdf = Vec::new();
    for (i,pos) in x.iter().enumerate() {
        let num = x_ord.iter().filter(|x| **x <= i).count() as f64;
        cdf.push((i, num/ln,));
    }
    println!("Len: {ln} Len cdf: {}", cdf.len());
    cdf
}

let tor_ps_path = "circs_torps";
let tor_gen_path = "circs_generated";
let tor_ps_circs_str = std::fs::read_to_string(&tor_ps_path).unwrap();
let tor_gen_circs_str = std::fs::read_to_string(&tor_gen_path).unwrap();
let tor_ps_circs : Vec<CircSerde> = serde_json::from_str(&tor_ps_circs_str).unwrap();
let tor_gen_circs : Vec<CircSerde> = serde_json::from_str(&tor_gen_circs_str).unwrap();
let relay_map = circs_to_map(&tor_gen_circs, &tor_ps_circs);

let tor_ps_vec: Vec<usize> = relay_map.values().cloned().map(|x| x.torps).collect();
let tor_ps_cdf : Vec<(usize, f64)> = cdf(&tor_ps_vec);

let tor_gen_vec: Vec<usize> = relay_map.values().cloned().map(|x| x.gen).collect();
let tor_gen_cdf : Vec<(usize, f64)> = cdf(&tor_gen_vec);
//let (relay_histo, max_count) = map_to_combined_histo(&relay_map);

evcxr_figure((2048, 1080), |root| {
    // The following code will create a chart context
    let mut chart = ChartBuilder::on(&root)
            .caption(format!("CDF for TorPS"), ("Arial", 20).into_font())
            .x_label_area_size(40)
            .y_label_area_size(40)
            .build_cartesian_2d(0usize..tor_ps_vec.len(), 0f64..1f64)?;
        chart.configure_mesh()
            .disable_x_mesh()
            .disable_y_mesh()
            .y_labels(5)
            .draw()?;

    
    chart.draw_series(
        tor_ps_cdf.iter().map(|(idx, torps)| Circle::new((*idx,*torps), 1, &BLUE)),
    )
    .unwrap();
    chart.draw_series(
        tor_gen_cdf.iter().map(|(idx, torgen)| Circle::new((*idx,*torgen), 1, &RED)),
    )
    .unwrap();
    

    Ok(())
}).style("width:100%")

Len: 4693 Len cdf: 4693
Len: 4693 Len cdf: 4693


CDF for TorPS
 
 
 
0.0
 
 
 
0.5
 
 
 
1.0
 
 
 
 
0
 
 
 
500
 
 
 
1000
 
 
 
1500
 
 
 
2000
 
 
 
2500
 
 
 
3000
 
 
 
3500
 
 
 
4000
 
 
 
4500
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
